In [ ]:
pip install altair_saver

In [ ]:
# Import packages
import numpy as np
import pandas as pd
import altair as alt
from altair_saver import save

In [ ]:
# Load dataset
df = pd.read_csv('/content/drive/My Drive/VisEMAp/ForcaTrabalho.csv', dtype = {'Trimestre (Código)': str}, encoding='latin-1')
df.tail()

Nível Territorial (Código)  ... PercentualDesocupapdo
1150                           3  ...              0.131783
1151                           3  ...              0.125452
1152                           3  ...              0.136638
1153                           3  ...              0.155251
1154                           3  ...              0.156371

[5 rows x 15 columns]

In [ ]:
df['NumTrimestre'] = df['Trimestre'].str[:1]
df['Ano'] = df['Trimestre (Código)'].str[:4]
df.head() 

Nível Territorial (Código) Nível Territorial  ...  NumTrimestre   Ano
0                           1            Brasil  ...             1  2012
1                           1            Brasil  ...             2  2012
2                           1            Brasil  ...             3  2012
3                           1            Brasil  ...             4  2012
4                           1            Brasil  ...             1  2013

[5 rows x 17 columns]

In [ ]:
# Dados grande região e unidade da federação
# Centro-Oeste, fonte: https://sidra.ibge.gov.br/territorio#/N3/IN%20N2%205
CO = pd.read_excel('/content/drive/My Drive/VisEMAp/Unidade da Federação em Grande Região - Centro-Oeste.xlsx', names=['Brasil, Grande Região e Unidade da Federação (Código)', 'Brasil, Grande Região e Unidade da Federação'], header = None)
CO['Grande Região (Código)'] = 5
CO['Grande Região'] = "Centro-Oeste"

# Nordeste, fonte: https://sidra.ibge.gov.br/territorio#/N3/IN%20N2%202
NE = pd.read_excel('/content/drive/My Drive/VisEMAp/Unidade da Federação em Grande Região - Nordeste.xlsx', names=['Brasil, Grande Região e Unidade da Federação (Código)', 'Brasil, Grande Região e Unidade da Federação'], header = None)
NE['Grande Região (Código)'] = 2
NE['Grande Região'] = "Nordeste"

# Norte, fonte: https://sidra.ibge.gov.br/territorio#/N3/IN%20N2%201
NO = pd.read_excel('/content/drive/My Drive/VisEMAp/Unidade da Federação em Grande Região - Norte.xlsx', names=['Brasil, Grande Região e Unidade da Federação (Código)', 'Brasil, Grande Região e Unidade da Federação'], header = None)
NO['Grande Região (Código)'] = 1
NO['Grande Região'] = "Norte"

# Sudeste, fonte: https://sidra.ibge.gov.br/territorio#/N3/IN%20N2%203
SE = pd.read_excel('/content/drive/My Drive/VisEMAp/Unidade da Federação em Grande Região - Sudeste.xlsx', names=['Brasil, Grande Região e Unidade da Federação (Código)', 'Brasil, Grande Região e Unidade da Federação'], header = None)
SE['Grande Região (Código)'] = 3
SE['Grande Região'] = "Sudeste"

# Sul, fonte: https://sidra.ibge.gov.br/territorio#/N3/IN%20N2%204
SU = pd.read_excel('/content/drive/My Drive/VisEMAp/Unidade da Federação em Grande Região - Sul.xlsx', names=['Brasil, Grande Região e Unidade da Federação (Código)', 'Brasil, Grande Região e Unidade da Federação'], header = None)
SU['Grande Região (Código)'] = 4
SU['Grande Região'] = "Sul"

GrandeRegiao = SU.append(SE.append(NO.append(NE.append(CO, ignore_index = True), ignore_index = True), ignore_index = True), ignore_index = True)
GrandeRegiao

Brasil, Grande Região e Unidade da Federação (Código)  ... Grande Região
0                                                  41      ...           Sul
1                                                  42      ...           Sul
2                                                  43      ...           Sul
3                                                  31      ...       Sudeste
4                                                  32      ...       Sudeste
5                                                  33      ...       Sudeste
6                                                  35      ...       Sudeste
7                                                  11      ...         Norte
8                                                  12      ...         Norte
9                                                  13      ...         Norte
10                                                 14      ...         Norte
11                                                 15      ...         Norte
12                                                 16      ...         Norte
13                                                 17      ...         Norte
14                                                 21      ...      Nordeste
15                                                 22      ...      Nordeste
16                                                 23      ...      Nordeste
17                                                 24      ...      Nordeste
18                                                 25      ...      Nordeste
19                                                 26      ...      Nordeste
20                                                 27      ...      Nordeste
21                                                 28      ...      Nordeste
22                                                 29      ...      Nordeste
23                                                 50      ...  Centro-Oeste
24                                                 51      ...  Centro-Oeste
25                                                 52      ...  Centro-Oeste
26                                                 53      ...  Centro-Oeste

[27 rows x 4 columns]

In [ ]:
# Adicionar grande região ao dataset original
df1 = pd.merge(df,GrandeRegiao,on=['Brasil, Grande Região e Unidade da Federação (Código)','Brasil, Grande Região e Unidade da Federação'],how='left')
df1['Grande Região'].fillna("Brasil", inplace = True) 
#df1[df1['Brasil, Grande Região e Unidade da Federação'] == 'Brasil']
df1.tail()

Nível Territorial (Código)  ... Grande Região
1150                           3  ...  Centro-Oeste
1151                           3  ...  Centro-Oeste
1152                           3  ...  Centro-Oeste
1153                           3  ...  Centro-Oeste
1154                           3  ...  Centro-Oeste

[5 rows x 19 columns]

In [ ]:
# Remove regions
df2 = df1[df1['Nível Territorial (Código)'] != 2]
df2['Força de trabalho (média móvel)'] = df2.groupby('Brasil, Grande Região e Unidade da Federação')['Força de trabalho'].rolling(4).mean().reset_index(0,drop=True)
df2['Força de trabalho - desocupada (média móvel)'] = df2.groupby('Brasil, Grande Região e Unidade da Federação')['Força de trabalho - desocupada'].rolling(4).mean().reset_index(0,drop=True)
df2['PercentualDesocupapdoMovel'] = df2['Força de trabalho - desocupada (média móvel)']/df2['Força de trabalho (média móvel)']

# Adicionar variação percentual da média móvel
#df2['PercentualDesocupapdoMovelVariacaoPercentual'] = (df2.groupby('Brasil, Grande Região e Unidade da Federação')['PercentualDesocupapdoMovel'].apply(pd.Series.pct_change)*100)
df2['PercentualDesocupapdoMovelVariacaoPercentual'] = (df2.groupby('Brasil, Grande Região e Unidade da Federação')['PercentualDesocupapdoMovel'].apply(pd.Series.diff)*100)
df2['PercentualDesocupapdoVariacaoPercentual'] = (df2.groupby('Brasil, Grande Região e Unidade da Federação')['PercentualDesocupapdo'].apply(pd.Series.diff)*100)

# Remover primeiros trimestre onde não é possível calcular a variação da média móvel.
df2 = df2.dropna(subset=['PercentualDesocupapdoMovelVariacaoPercentual'])

df2.head()


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Nível Territorial (Código)  ... PercentualDesocupapdoVariacaoPercentual
4                           1  ...                                1.113693
5                           1  ...                               -0.543010
6                           1  ...                               -0.494737
7                           1  ...                               -0.756499
8                           1  ...                                0.987234

[5 rows x 24 columns]

In [ ]:
# Preparar dataset adicionando coluna com a média de variação da taxa por estado para ordenar o gráfico

meanEstado = df2.groupby('Brasil, Grande Região e Unidade da Federação')['PercentualDesocupapdo'].mean().reset_index()
meanEstado.rename(columns={'PercentualDesocupapdo': 'MediaPercentualDesocupapdo'}, inplace=True)
#meanEstado

stdEstado = df2.groupby('Brasil, Grande Região e Unidade da Federação')['PercentualDesocupapdo'].std().reset_index()
stdEstado.rename(columns={'PercentualDesocupapdo': 'StdPercentualDesocupapdo'}, inplace=True)
#stdEstado

# Adicionar média da variação por estado ao dataset original
df2 = pd.merge(df2,meanEstado,on=['Brasil, Grande Região e Unidade da Federação'],how='left')
df2 = pd.merge(df2,stdEstado,on=['Brasil, Grande Região e Unidade da Federação'],how='left')

df2['minPercentualDesocupapdo'] = df2['MediaPercentualDesocupapdo'] - df2['StdPercentualDesocupapdo']/2
df2['maxPercentualDesocupapdo'] = df2['MediaPercentualDesocupapdo'] + df2['StdPercentualDesocupapdo']/2

df2.tail()

Nível Territorial (Código)  ... maxPercentualDesocupapdo
863                           3  ...                 0.127632
864                           3  ...                 0.127632
865                           3  ...                 0.127632
866                           3  ...                 0.127632
867                           3  ...                 0.127632

[5 rows x 28 columns]

In [ ]:
# Gráfico da da taxa de desemprego
# Selection tool
selection = alt.selection_single(fields=['Brasil, Grande Região e Unidade da Federação'])
# Color change when clicked
color = alt.condition(selection,
                    alt.Color('Brasil, Grande Região e Unidade da Federação:N'),
                    alt.value('lightgray'))

base = alt.Chart(df2).mark_line().encode(
    x= alt.X('Trimestre (Código):N', title='Trimestre (ano + número do trimestre)'),
    y= alt.Y('PercentualDesocupapdo:Q', title='Percentual de desocupados na força de trabalho', axis=alt.Axis(format='%')),
    color='Brasil, Grande Região e Unidade da Federação'
)

# Chart
chart = base.encode(
  color=alt.condition(selection, 'Brasil, Grande Região e Unidade da Federação:N', alt.value('lightgray')),
  tooltip=['Brasil, Grande Região e Unidade da Federação', 'Trimestre', 'Unidade de Medida', 'Força de trabalho', 'Força de trabalho - desocupada', 'PercentualDesocupapdo']
).add_selection(
  selection
).properties(
    title='Força de Trabalho Desocupada no Brasil'
)

# Overlay
overlay = base.encode(
  color='Brasil, Grande Região e Unidade da Federação',
  opacity=alt.value(0.5),
).transform_filter(
  selection
)

# Sum it all up
alt.layer(chart, overlay).configure_axis(
    labelFontSize=10,
    titleFontSize=12
).configure_title(
    fontSize=23
)

alt.LayerChart(...)

In [ ]:
# Heatmap da taxa de desemprego - NÃO MOSTRA NENHUMA NOVIDADE

selection = alt.selection_multi(fields=['Grande Região'], bind='legend')

# Título geral
title = alt.Chart(
    {"values": [{"text": "The Title"}]}
).mark_text(size=20).encode(
    text="text:N"
)

# gráfico das taxas de desemprego
# Tooltip https://vegawidget.github.io/altair/articles/tooltips.html
points = alt.Chart(data= df2, width=620, height=500, title='Taxa de Desemprego (TD) - %').mark_rect(filled=True).encode(
    x= alt.X('Trimestre', type='nominal', title='Trimestre', sort = alt.SortField('Trimestre (Código)', order='ascending')),
    y = alt.Y('Brasil, Grande Região e Unidade da Federação', title='Estado'), #, sort = alt.SortField("MediaPercentualDesocupapdo", order = "ascending")
    tooltip = [alt.Tooltip(field = "Brasil, Grande Região e Unidade da Federação", title = "Estado", type = "nominal"), 
                alt.Tooltip(field = "Grande Região", title = "Região", type = "nominal"),
                alt.Tooltip(field = "Trimestre", type = "nominal"),
                alt.Tooltip(field = "PercentualDesocupapdo", title = 'Taxa de desemprego', format = ".2%", type = "quantitative"),
                alt.Tooltip(field = "PercentualDesocupapdoVariacaoPercentual", title = 'Variação da Taxa de desemprego', format = ".1f", type = "quantitative")],
    color=alt.condition(selection, 
                        alt.Color('PercentualDesocupapdo:Q', #scale=alt.Scale(scheme='blueorange'), domain=[-20, 20]
                          legend=alt.Legend(direction='vertical', orient='left', legendY=30, title = None)),
                        alt.value('lightgray'))
  ).add_selection(
    selection
  )

points


alt.Chart(...)

In [ ]:
# Heatmap da variação da taxa de desemprego sem MÉDIA MÓVEL - NÃO MOSTRA PADRÃO NENHUM

selection = alt.selection_multi(fields=['Grande Região'], bind='legend')

# Título geral
title = alt.Chart(
    {"values": [{"text": "The Title"}]}
).mark_text(size=20).encode(
    text="text:N"
)

# gráfico das taxas de desemprego
# Tooltip https://vegawidget.github.io/altair/articles/tooltips.html
points = alt.Chart(data= df2, width=620, height=500, title='Variação Trimestral da Taxa de Desemprego (TD) - pontos percentuais').mark_rect(filled=True).encode(
    x= alt.X('Trimestre', type='nominal', title='Trimestre', sort = alt.SortField('Trimestre (Código)', order='ascending')),
    y = alt.Y('Brasil, Grande Região e Unidade da Federação', title='Estado'),
    tooltip = [alt.Tooltip(field = "Brasil, Grande Região e Unidade da Federação", title = "Estado", type = "nominal"), 
                alt.Tooltip(field = "Grande Região", title = "Região", type = "nominal"),
                alt.Tooltip(field = "Trimestre", type = "nominal"),
                alt.Tooltip(field = "PercentualDesocupapdo", title = 'Taxa de desemprego', format = ".2%", type = "quantitative"),
                alt.Tooltip(field = "PercentualDesocupapdoVariacaoPercentual", title = 'Variação da Taxa de desemprego', format = ".1f", type = "quantitative")],
    color=alt.condition(selection, 
                        alt.Color('PercentualDesocupapdoVariacaoPercentual:Q', scale=alt.Scale(scheme='blueorange'), #, domain=[-20, 20]
                          legend=alt.Legend(direction='vertical', orient='left', legendY=30, title = None)),
                        alt.value('lightgray'))
  ).add_selection(
    selection
  )

points


alt.Chart(...)

In [ ]:
# Gráfico da média móvel da taxa de desemprego
# Selection tool
selection = alt.selection_single(fields=['Brasil, Grande Região e Unidade da Federação'])
# Color change when clicked
color = alt.condition(selection,
                    alt.Color('Brasil, Grande Região e Unidade da Federação:N'),
                    alt.value('lightgray'))

base = alt.Chart(df2).mark_line().encode(
    x= alt.X('Trimestre (Código)', title='Trimestre (ano + número do trimestre)'),
    y= alt.Y('PercentualDesocupapdoMovel', title='Média móvel do percentual de desocupados na força de trabalho', axis=alt.Axis(format='%')),
    color='Brasil, Grande Região e Unidade da Federação'
)

# Chart
chart = base.encode(
  color=alt.condition(selection, 'Brasil, Grande Região e Unidade da Federação:N', alt.value('lightgray')),
  tooltip=['Brasil, Grande Região e Unidade da Federação', 'Trimestre', 'Unidade de Medida', 'Força de trabalho', 'Força de trabalho - desocupada', 'PercentualDesocupapdo', 'PercentualDesocupapdoMovel']
).add_selection(
  selection
).properties(
    title='Força de Trabalho Desocupada no Brasil'
)

# Overlay
overlay = base.encode(
  color='Brasil, Grande Região e Unidade da Federação',
  opacity=alt.value(0.5),
).transform_filter(
  selection
)

# Sum it all up
alt.layer(chart, overlay).configure_axis(
    labelFontSize=10,
    titleFontSize=12
).configure_title(
    fontSize=23
)

alt.LayerChart(...)

In [ ]:
# Heatmap da variação percentual da média móvel 

# alterar texto para melhorar eixo x
df2["Trimestre"]= df2["Trimestre"].str.replace("trimestre", "-")

# radio/dropdown/slider https://altair-viz.github.io/gallery/multiple_interactions.html e alterar posição https://stackoverflow.com/questions/62103632/altair-change-the-position-of-a-slider 
df2.rename(columns={"Grande Região": "regiao"}, inplace = True)
#selection = alt.selection_multi(fields=['Clique na região']) #, bind='legend'
regiao_radio = alt.binding_radio(options=np.append([None],df2['regiao'].unique()),labels=['Todas'])
selection = alt.selection_single(fields=['regiao'], bind=regiao_radio, name="Selecione")

# Título geral
title = alt.Chart(
    {"values": [{"text": "The Title"}]}
).mark_text(size=20).encode(
    text="text:N"
)

# gráfico das taxas de desemprego
# Tooltip https://vegawidget.github.io/altair/articles/tooltips.html
points = alt.Chart(data= df2, width=620, height=500, title='Diferença da Taxa de Desemprego (TD) entre Trimestres - pontos percentuais').mark_rect(filled=True).encode(
    x= alt.X('Trimestre', type='nominal', title= 'Trimestre', sort = alt.SortField('Trimestre (Código)', order='ascending')),
    y = alt.Y('Brasil, Grande Região e Unidade da Federação', title=None, sort = alt.SortField("MediaPercentualDesocupapdo", order = "descending")),
    tooltip = [alt.Tooltip(field = "Brasil, Grande Região e Unidade da Federação", title = "Estado", type = "nominal"), 
                alt.Tooltip(field = "regiao", title = "Região", type = "nominal"),
                alt.Tooltip(field = "Trimestre", type = "nominal"),
                alt.Tooltip(field = "PercentualDesocupapdoMovel", title = 'Taxa de desemprego (média móvel)', format = ".2%", type = "quantitative"),
                alt.Tooltip(field = "PercentualDesocupapdoMovelVariacaoPercentual", title = 'Diferença da Taxa de desemprego (média móvel) em relação ao trimestre anterior', format = ".1f", type = "quantitative")],
    color=alt.condition(selection, 
                        alt.Color('PercentualDesocupapdoMovelVariacaoPercentual:Q', scale=alt.Scale(scheme='blueorange', domain=[-1.8, 1.8]), 
                          legend=alt.Legend(direction='vertical', orient='left', legendY=30, title = 'Diferença da taxa (pontos percentuais)', titleOrient = 'left', titleFontSize = 10, titleFontWeight = 'normal')),
                        alt.value('lightgray'))
  ).add_selection(
    selection
  )

# Adicionar linhas 

# para o Brasil
rule = alt.Chart(df2).mark_rule(
    color="lightgray",
    strokeWidth=0.5,
    strokeDash=[2, 2]
).encode(
    y = alt.Y('Brasil, Grande Região e Unidade da Federação', sort = alt.SortField("MediaPercentualDesocupapdo", order = "descending"))
).transform_filter(alt.datum['Brasil, Grande Região e Unidade da Federação'] == "Brasil")

# para pandemia
rulePandemia = alt.Chart(df2).mark_rule(
    color="darkred",
    strokeWidth=0.5,
    strokeDash=[5, 5]
).encode(
    x = alt.X('Trimestre', sort = alt.SortField('Trimestre (Código)', order='ascending'))
).transform_filter(alt.datum['Trimestre (Código)'] == '202001')

textPandemia = alt.Chart({'values':[{'Trimestre': "2º - 2019", 'Brasil, Grande Região e Unidade da Federação': "Santa Catarina"}]}).mark_text(
    text ='Início da pandemia ->', 
    angle = 0, 
    color = "darkred"
).encode(
    x= alt.X('Trimestre:N', sort = alt.SortField('Trimestre (Código)', order='ascending')),
    y= alt.Y('Brasil, Grande Região e Unidade da Federação:N', sort = alt.SortField("MediaPercentualDesocupapdo", order = "descending"))
)


# Error bar para taxa de desemprego por estado
# Color schemes https://vega.github.io/vega/docs/schemes/
# Ajustes https://nextjournal.com/sdanisch/scales-axes-and-legends
# *Error bar with min and max https://altair-viz.github.io/gallery/simple_scatter_with_errorbars.html , https://vega.github.io/vega-lite/docs/errorbar.html

bars = alt.Chart(df2, width=100, height=500).mark_errorbar().encode(
    x=alt.X('minPercentualDesocupapdo:Q', scale=alt.Scale(zero=False), axis=alt.Axis(orient='bottom', format='%'), title = None),
    x2='maxPercentualDesocupapdo:Q',
    y=alt.Y('Brasil, Grande Região e Unidade da Federação:N', sort = alt.SortField("MediaPercentualDesocupapdo", order = "descending"), axis=alt.Axis(orient='right'), title=None),
    color=alt.condition(selection, alt.value('black'), alt.value('lightgray'))
  ).add_selection(
    selection
  )


dots = alt.Chart(df2, width=100, height=500, title='TD (média) - %').mark_point(filled=True, color='black').encode(
  x=alt.X('MediaPercentualDesocupapdo:Q', axis=alt.Axis(orient='bottom')),
  y=alt.Y('Brasil, Grande Região e Unidade da Federação:N', sort = alt.SortField("MediaPercentualDesocupapdo", order = "descending"), axis=alt.Axis(orient='right'), title=None),
    tooltip = [alt.Tooltip(field = "Brasil, Grande Região e Unidade da Federação", title = "Estado", type = "nominal"), 
                alt.Tooltip(field = "regiao", title = "Região", type = "nominal"),
                alt.Tooltip(field = "MediaPercentualDesocupapdo", title = 'Média da Taxa de desemprego', format = ".2%", type = "quantitative"),
                alt.Tooltip(field = "StdPercentualDesocupapdo", title = 'Desvio padrão da Taxa de desemprego', format = ".2%", type = "quantitative")],
    #shape = alt.Shape('regiao:N', scale=alt.Scale(range=['square', 'triangle-up', 'triangle-right', 'triangle-down', 'triangle-left', 'circle'])),
    color = alt.condition(selection, alt.value('black'), alt.value('lightgray'))
  ).add_selection(
    selection
  )

chart = alt.hconcat(alt.layer(points, rule, rulePandemia, textPandemia), alt.layer(bars,dots), spacing=0).resolve_legend()

chartfinal = chart.properties(
    title={
      "text": ["Desemprego em estados acompanham crises de diferentes formas e intensidade"], 
      "subtitle": ["Crise desencadeada em meados 2014 e início da pandemia pela Covid-19 em 2020, veja as correlações. Bahia tem maior média da taxa de desemprego e Roraima aparenta ser outro país.",
                   "(Taxa = média móvel do percentual de desocupados de 4 trimestres, Diferença = taxa do trimestre atual - taxa do trimestre anterior * 100, Fonte = PNAD Contínua, IBGE)"," "," "],
      "color": 'rgb(31,93,151)',
      "fontSize": 25,
      "subtitleColor": 'rgb(161,80,8)'
    }
)

chartfinal
#save(chartfinal, "chartfinal2.html")

# Depois do gráfico salvo, adicionar seguinte código no HTML conforme https://stackoverflow.com/questions/62103632/altair-change-the-position-of-a-slider
#<style>
#form.vega-bindings {
#  position: absolute;
#  right: 568px;
#  top: 63px;
#}
#</style>


alt.HConcatChart(...)